# Training LeNet-5 on CIFAR-10
In this notebook, we will try to deploy the famous LeNet-5 to solve a simple image classification task, the CIFAR-10. CIFAR-10 is composed of 60K images from 10 categories. After splitting the dataset, we have 45K/5K/10K images for train/valiation/test dataset.
In this notebook, only the labels of training/validation dataset is visible to you, so you can use the training and validation data to tune your model. After you submitted your model, your final grade will be determined on the model performance on the holdout test dataset.

### Step 0 Setting up LeNet-5 model
As you have set up the LeNet-5 model in Homework 1, we will just move the implementation of LeNet-5 model here, so you can use it for this homework.

In [1]:
import argparse
import os, sys
import time
import datetime

# Import pytorch dependencies
import torch
import torch.nn as nn
import torch.nn.functional as F
import torchvision
import torchvision.transforms as transforms
import torch.optim as optim
from tqdm import tqdm_notebook as tqdm

In [2]:
import math
# Create the neural network module: LeNet-5
class LeNet5(nn.Module):
    def __init__(self):
        super(LeNet5, self).__init__()
        self.conv1 = nn.Conv2d(3, 6, 5)
        self.conv2 = nn.Conv2d(6, 16, 5)
        self.fc1   = nn.Linear(16*5*5, 120)
        self.fc2   = nn.Linear(120, 84)
        self.fc3   = nn.Linear(84, 10)
        # self._initialize_weights()

    def forward(self, x):
        out = F.relu(self.conv1(x))
        out = F.max_pool2d(out, 2)
        out = F.relu(self.conv2(out))
        out = F.max_pool2d(out, 2)
        out = out.view(out.size(0), -1)
        out = F.relu(self.fc1(out))
        print(len(out),out)
        out = F.relu(self.fc2(out))
        out = self.fc3(out)
        return out

    """
    def _initialize_weights(self):
        for m in self.modules():
            if isinstance(m, nn.Conv2d):
                n = m.kernel_size[0] * m.kernel_size[1] * (m.in_channels + m.out_channels)
                m.weight.data.normal_(0, math.sqrt(2. / n))
                if m.bias is not None:
                    m.bias.data.zero_()
            elif isinstance(m, nn.BatchNorm2d):
                m.weight.data.fill_(1)
                m.bias.data.zero_()
            elif isinstance(m, nn.Linear):
                n = m.weight.size(1)
                m.weight.data.normal_(0, 0.01)
                m.bias.data.zero_() """

### Step 1: Setting up preprocessing functions.
Preprocessing is very important because it prepares your data for proceeding training steps.
Write functions to load dataset and preprocess the incoming data. We recommend that the preprocess scheme \textbf{must} include normalize, standardization, batch shuffling to make sure the training 
process goes smoothly. The preprocess scheme may also contain some data augmentation methods 
(e.g., random crop, random flip, etc.). 

Reference value for mean/std:

**mean(RGB-format): (0.4914, 0.4822, 0.4465)**

**std(RGB-format): (0.2023, 0.1994, 0.2010)**

In [3]:
# Specify preprocessing function.
# Reference mean/std value for 
transform_train  = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010)),
    ])

transform_val = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010)),
    ])



### Step 2: Setting up data I/O
Data I/O reads data from the dataset and prepares it for further procedures. Note that you have to link transformation with data I/O so that these operations can be interleaved. Thus, the training process can be more efficient.

In [4]:
# You cannot change this line.
from tools.dataloader import CIFAR10
# Call the dataset Loader
DATAROOT = "./data"
TRAIN_BATCH_SIZE = 128
VAL_BATCH_SIZE = 100
trainset = CIFAR10(root=DATAROOT, train=True, download=True, transform=transform_train)
trainloader = torch.utils.data.DataLoader(trainset, batch_size=TRAIN_BATCH_SIZE, shuffle=True, num_workers=4)
valset = CIFAR10(root=DATAROOT, train=False, download=True, transform=transform_val)
valloader = torch.utils.data.DataLoader(valset, batch_size=VAL_BATCH_SIZE, shuffle=False, num_workers=4)

Using downloaded and verified file: ./data/cifar10_trainval_F20.zip
Extracting ./data/cifar10_trainval_F20.zip to ./data
Files already downloaded and verified
Training dataset has 45000 examples!
Using downloaded and verified file: ./data/cifar10_trainval_F20.zip
Extracting ./data/cifar10_trainval_F20.zip to ./data
Files already downloaded and verified
Validation dataset has 5000 examples!


### Step 3: Instantialize your LeNet-5 model and deploy it to GPU devices.
You may want to deploy your model to GPU device for efficient training. Please assign your model to GPU if possible. If you are training on a machine without GPUs, please deploy your model to CPUs.

In [5]:
# Specify the device for computation
device = 'cuda' if torch.cuda.is_available() else 'cpu'
net = LeNet5()
net = net.to(device)
if device =='cuda':
    print("Train on GPU...")
else:
    print("Train on CPU...")

Train on CPU...


### Hyperparameter settings
Hyperparameters are quite crucial in determining the performance of our model. The default hyperparameter settings are sufficient for a decent result. You may tune them wisely and carefully for better results.

In [6]:
# Initial learning rate
INITIAL_LR = 0.01
# Momentum for optimizer.
MOMENTUM = 0.9
# Regularization
REG = 1e-4
# Total number of training epochs
EPOCHS = 30
# Learning rate decay policy.
DECAY_EPOCHS = 2
DECAY = 1.00

### Handling weights load/save protocols.
This handles the weight loading/saving protocols.You may be able to load from checkpoints.

In [7]:
CHECKPOINT_PATH = "./saved_model"
# FLAG for loading the pretrained model
TRAIN_FROM_SCRATCH = True
# Code for loading checkpoint and recover epoch id.
CKPT_PATH = "./saved_model/model.h5"
def get_checkpoint(ckpt_path):
    try:
        ckpt = torch.load(ckpt_path)
    except Exception as e:
        print(e)
        return None
    return ckpt

ckpt = get_checkpoint(CKPT_PATH)
if ckpt is None or TRAIN_FROM_SCRATCH:
    if not TRAIN_FROM_SCRATCH:
        print("Checkpoint not found.")
    print("Training from scratch ...")
    start_epoch = 0
    current_learning_rate = INITIAL_LR
else:
    print("Successfully loaded checkpoint: %s" %CKPT_PATH)
    net.load_state_dict(ckpt['net'])
    start_epoch = ckpt['epoch'] + 1
    current_learning_rate = ckpt['lr']
    print("Starting from epoch %d " %start_epoch)

print("Starting from learning rate %f:" %current_learning_rate)

Training from scratch ...
Starting from learning rate 0.010000:


### Step 4 Setting up loss functions and Optimizers
Loss function is your objective to train the neural networks. Typically, we use multi-class cross entropy as objectives for classification models (e.g., CIFAR-10, MNIST). In this homework, we use SGD optimizer with momentum as our optimizer. You need to formulate the cross-entropy loss function in PyTorch.
You should also specify a PyTorch Optimizer to optimize this loss function.

In [8]:
# Create loss function and specify regularization
criterion = nn.CrossEntropyLoss()
# Add optimizer
optimizer = optim.SGD(params=net.parameters(), lr=current_learning_rate, momentum=MOMENTUM, weight_decay=REG, nesterov=False)

### Step 5: Start the training process.
Congratulations! You have completed all of the previous steps and it is time to train our neural network.
Training a neural network usually composes the following 3 parts: 

**i) Get a batch of data from the dataloader and copy it to your device (GPU)**

**ii) Do a forward pass to get the output logits from the neural network. Compute the forward loss.**

**iii) Do a backward pass (back-propagation) to compute gradients of all weights with respect to the loss.**

You will also need to compute accuracy within all these parts to justify that your model is doing well on the dataset.


In [9]:
# Start the training/validation process
# The process should take about 5 minutes on a GTX 1070-Ti
# if the code is written efficiently.
global_step = 0
best_val_acc = 0

for i in range(start_epoch, EPOCHS):
    print(datetime.datetime.now())
    # Switch to train mode
    net.train()
    print("Epoch %d:" %i)

    total_examples = 0
    correct_examples = 0

    train_loss = 0
    train_acc = 0
    
    # Train the training dataset for 1 epoch.
    for batch_idx, (inputs, targets) in enumerate(trainloader):
        # Copy inputs to device
        inputs = inputs.to(device)
        targets = targets.to(device)
        # Zero the gradient
        optimizer.zero_grad()
        # Generate output
        outputs = net(inputs)
        loss = criterion(outputs, targets)
        
#         if i==0:
#             print('target',targets)
#             print('output',outputs)
#             print('initial loss: ',loss)

        # Now backward loss
        loss.backward()
        # Apply gradient
        optimizer.step()
        # Calculate predicted labels
        _, predicted = outputs.max(1)
        total_examples += predicted.size(0)
        correct_examples += predicted.eq(targets).sum().item()
        train_loss += loss
        global_step += 1
                
    avg_loss = train_loss / (batch_idx + 1)
    avg_acc = correct_examples / total_examples
    print("Training loss: %.4f, Training accuracy: %.4f" %(avg_loss, avg_acc))
    print(datetime.datetime.now())
    # Validate on the validation dataset
    print("Validation...")
    total_examples = 0
    correct_examples = 0
    
    net.eval()

    val_loss = 0
    val_acc = 0
    # Disable gradient during validation
    with torch.no_grad():
        for batch_idx, (inputs, targets) in enumerate(valloader):
            # Copy inputs to device
            inputs = inputs.to(device)
            targets = targets.to(device)
            # Zero the gradient
            optimizer.zero_grad()
            # Generate output from the DNN.
            outputs = net(inputs)
            loss = criterion(outputs, targets)            
            # Calculate predicted labels
            _, predicted = outputs.max(1)
            total_examples += predicted.size(0)
            correct_examples += predicted.eq(targets).sum().item()
            val_loss += loss

    avg_loss = val_loss / len(valloader)
    avg_acc = correct_examples / total_examples
    
    print("Validation loss: %.4f, Validation accuracy: %.4f" % (avg_loss, avg_acc))

    # Handle the learning rate scheduler.
    if i % DECAY_EPOCHS == 0 and i != 0:
        current_learning_rate = current_learning_rate * DECAY
        for param_group in optimizer.param_groups:
            param_group['lr'] = current_learning_rate
        print("Current learning rate has decayed to %f" %current_learning_rate)
    
    # Save for checkpoint
    if avg_acc > best_val_acc:
        best_val_acc = avg_acc
        if not os.path.exists(CHECKPOINT_PATH):
            os.makedirs(CHECKPOINT_PATH)
        print("Saving ...")
        state = {'net': net.state_dict(),
                 'epoch': i,
                 'lr': current_learning_rate}
        torch.save(state, os.path.join(CHECKPOINT_PATH, 'model.h5'))

print("Optimization finished.")

2020-09-15 00:31:17.740483
Epoch 0:
128 tensor([[0.0198, 0.1223, 0.1093,  ..., 0.2592, 0.0000, 0.1740],
        [0.0071, 0.0408, 0.0543,  ..., 0.1975, 0.0139, 0.3821],
        [0.0000, 0.1022, 0.0518,  ..., 0.4275, 0.0159, 0.1819],
        ...,
        [0.2473, 0.1280, 0.1502,  ..., 0.3394, 0.0000, 0.2089],
        [0.0510, 0.0000, 0.0673,  ..., 0.0175, 0.0000, 0.2299],
        [0.0732, 0.1235, 0.0774,  ..., 0.1783, 0.0000, 0.2087]],
       grad_fn=<ReluBackward0>)
128 tensor([[0.0000, 0.1807, 0.1413,  ..., 0.4055, 0.0000, 0.2892],
        [0.1011, 0.0658, 0.1329,  ..., 0.1221, 0.0000, 0.1799],
        [0.1039, 0.1732, 0.0959,  ..., 0.1204, 0.0418, 0.0672],
        ...,
        [0.0530, 0.0000, 0.0826,  ..., 0.3053, 0.0000, 0.1734],
        [0.0686, 0.1720, 0.1554,  ..., 0.2217, 0.0000, 0.1900],
        [0.2290, 0.1910, 0.0581,  ..., 0.1405, 0.0000, 0.1912]],
       grad_fn=<ReluBackward0>)
128 tensor([[0.0000, 0.0000, 0.0169,  ..., 0.1788, 0.0000, 0.2091],
        [0.0469, 0.0000, 0.0

128 tensor([[0.0320, 0.1090, 0.0327,  ..., 0.0005, 0.0000, 0.1156],
        [0.1058, 0.0000, 0.1449,  ..., 0.0896, 0.0258, 0.1593],
        [0.0442, 0.0093, 0.1001,  ..., 0.3292, 0.0000, 0.1962],
        ...,
        [0.0233, 0.0158, 0.0513,  ..., 0.2191, 0.0916, 0.1799],
        [0.0231, 0.2347, 0.1108,  ..., 0.1358, 0.0000, 0.1344],
        [0.0000, 0.0000, 0.0084,  ..., 0.1676, 0.0031, 0.1900]],
       grad_fn=<ReluBackward0>)
128 tensor([[0.0715, 0.1716, 0.0158,  ..., 0.2720, 0.1507, 0.1152],
        [0.0422, 0.2135, 0.0925,  ..., 0.2393, 0.0291, 0.0769],
        [0.0246, 0.0870, 0.1024,  ..., 0.2070, 0.0000, 0.2263],
        ...,
        [0.0779, 0.0550, 0.0000,  ..., 0.1568, 0.1728, 0.1448],
        [0.1400, 0.0614, 0.1759,  ..., 0.1550, 0.0000, 0.1048],
        [0.1174, 0.0000, 0.0532,  ..., 0.2444, 0.0000, 0.2076]],
       grad_fn=<ReluBackward0>)
128 tensor([[0.1000, 0.0069, 0.0168,  ..., 0.2032, 0.0000, 0.2207],
        [0.0217, 0.0957, 0.1076,  ..., 0.3519, 0.0000, 0.3074],


128 tensor([[0.0879, 0.0522, 0.0742,  ..., 0.1170, 0.0173, 0.0652],
        [0.0000, 0.0000, 0.0232,  ..., 0.2517, 0.0000, 0.2126],
        [0.0000, 0.0802, 0.0582,  ..., 0.3413, 0.1910, 0.3217],
        ...,
        [0.0000, 0.0000, 0.0291,  ..., 0.1446, 0.0527, 0.2423],
        [0.1501, 0.1728, 0.0111,  ..., 0.3688, 0.0076, 0.2211],
        [0.0000, 0.1377, 0.1710,  ..., 0.2515, 0.0169, 0.4804]],
       grad_fn=<ReluBackward0>)
128 tensor([[0.0316, 0.0000, 0.1325,  ..., 0.3803, 0.0000, 0.3756],
        [0.1569, 0.1829, 0.0000,  ..., 0.2134, 0.0000, 0.1432],
        [0.1490, 0.0000, 0.1550,  ..., 0.2865, 0.0000, 0.3888],
        ...,
        [0.0407, 0.1404, 0.1313,  ..., 0.2732, 0.0000, 0.1618],
        [0.0117, 0.0000, 0.1905,  ..., 0.2793, 0.0223, 0.0809],
        [0.0000, 0.0000, 0.0000,  ..., 0.4968, 0.1064, 0.1993]],
       grad_fn=<ReluBackward0>)
128 tensor([[0.1365, 0.0376, 0.0665,  ..., 0.1877, 0.0000, 0.2179],
        [0.0068, 0.3125, 0.1742,  ..., 0.2080, 0.0201, 0.4109],


128 tensor([[0.0000, 0.0154, 0.1037,  ..., 0.4324, 0.1067, 0.3520],
        [0.1866, 0.1179, 0.4136,  ..., 0.2808, 0.0063, 0.3113],
        [0.0231, 0.0899, 0.0589,  ..., 0.3285, 0.0215, 0.1767],
        ...,
        [0.1265, 0.0010, 0.2515,  ..., 0.3746, 0.0000, 0.1947],
        [0.0676, 0.0076, 0.1423,  ..., 0.1413, 0.0000, 0.2361],
        [0.1255, 0.1609, 0.0870,  ..., 0.1714, 0.0123, 0.1400]],
       grad_fn=<ReluBackward0>)
128 tensor([[0.1556, 0.0000, 0.1263,  ..., 0.3332, 0.0519, 0.3265],
        [0.1506, 0.0526, 0.2294,  ..., 0.1009, 0.1212, 0.2722],
        [0.0000, 0.1912, 0.1683,  ..., 0.1614, 0.0385, 0.2682],
        ...,
        [0.2403, 0.0000, 0.1405,  ..., 0.3445, 0.0395, 0.1126],
        [0.1923, 0.1917, 0.0925,  ..., 0.3173, 0.0000, 0.2681],
        [0.1533, 0.0527, 0.2513,  ..., 0.2907, 0.0000, 0.3112]],
       grad_fn=<ReluBackward0>)
128 tensor([[0.1747, 0.1164, 0.1899,  ..., 0.1431, 0.0000, 0.2496],
        [0.2827, 0.0151, 0.4085,  ..., 0.5527, 0.0000, 0.4125],


128 tensor([[0.2287, 0.1396, 0.1609,  ..., 0.0000, 0.0471, 0.3429],
        [0.0000, 0.1876, 0.0000,  ..., 0.2058, 0.3085, 0.3664],
        [0.1919, 0.0981, 0.0998,  ..., 0.7479, 0.5620, 0.2956],
        ...,
        [0.3129, 0.0961, 0.1685,  ..., 0.1729, 0.0000, 0.1985],
        [0.0000, 0.0505, 0.1055,  ..., 0.1745, 0.0856, 0.2071],
        [0.2831, 0.1046, 0.2044,  ..., 0.2199, 0.0000, 0.2769]],
       grad_fn=<ReluBackward0>)
128 tensor([[0.0867, 0.0000, 0.3021,  ..., 0.8535, 0.2205, 0.4584],
        [0.3007, 0.0105, 0.2259,  ..., 0.7766, 0.1006, 0.3812],
        [0.0000, 0.0000, 0.0000,  ..., 0.5991, 0.1599, 0.4554],
        ...,
        [0.2024, 0.1764, 0.2374,  ..., 0.4935, 0.0352, 0.3309],
        [0.0578, 0.0692, 0.1396,  ..., 0.1262, 0.2168, 0.1150],
        [0.1394, 0.0000, 0.1953,  ..., 0.3232, 0.1410, 0.2361]],
       grad_fn=<ReluBackward0>)
128 tensor([[0.1777, 0.0852, 0.1408,  ..., 0.1469, 0.0671, 0.0218],
        [0.3236, 0.0000, 0.4701,  ..., 0.7249, 0.3635, 0.4130],


...

128 tensor([[ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  3.8602,  0.0000],
        [ 4.3442,  0.0000,  0.0000,  ...,  0.0000,  1.2910,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        ...,
        [ 0.4512, 11.2313,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 5.1762,  0.0000,  0.0000,  ...,  3.8194,  0.0000, 11.7250],
        [ 2.3724,  8.3762,  1.7616,  ...,  0.0000,  0.0000,  0.0000]],
       grad_fn=<ReluBackward0>)
128 tensor([[ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000, 16.1910],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  2.4891],
        [ 0.0000,  8.6636,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        ...,
        [ 0.0000,  0.0000, 18.4558,  ...,  0.0000,  3.0032,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  4.6857,  0.0000],
        [ 0.0000,  0.0000,  3.6514,  ...,  1.6078,  0.0000,  5.2921]],
       grad_fn=<ReluBackward0>)
128 tensor([[ 3.8123,  0.0000,  0.0000,  ...,  0.0000,  5.11

128 tensor([[ 1.8940,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  5.0686],
        [ 7.9799,  0.0000,  0.0000,  ..., 10.4508,  0.4122,  5.6658],
        [ 0.0000,  3.9358,  0.0000,  ...,  2.0536,  0.0000,  8.8409],
        ...,
        [ 0.0000,  0.0000,  0.0000,  ..., 12.2108,  0.0000,  4.0370],
        [ 0.0000,  7.5310, 10.0720,  ...,  4.2650,  0.0000,  2.7262],
        [ 0.0000,  0.0000, 10.9838,  ..., 17.5751,  0.0000,  6.0804]],
       grad_fn=<ReluBackward0>)
128 tensor([[ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ..., 11.9051,  0.0000, 20.4414],
        [12.6932,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        ...,
        [14.2363,  0.0000,  0.0000,  ..., 12.4633,  0.0000,  0.0000],
        [19.9898,  0.0000,  0.1812,  ...,  6.7670, 25.4420,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000]],
       grad_fn=<ReluBackward0>)
128 tensor([[ 0.0000,  0.0000,  0.0000,  ...,  4.0640,  0.00

128 tensor([[ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.1527,  0.0000,  3.9632,  ...,  0.0000,  2.6660,  0.0000],
        [ 7.3908,  3.8865,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        ...,
        [ 2.1048,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  4.9458],
        [ 2.8197,  0.0000,  7.0326,  ...,  0.0000,  0.0000,  0.8805],
        [24.7933,  0.0000,  0.9631,  ...,  0.0000,  7.1663,  0.0000]],
       grad_fn=<ReluBackward0>)
128 tensor([[ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  1.3907],
        [ 7.1823,  0.0000,  0.0000,  ...,  1.1246, 11.3411,  0.0000],
        [ 4.1094,  0.0000,  0.0000,  ...,  0.0000,  1.6447,  0.0000],
        ...,
        [ 0.0000,  1.8105,  0.0000,  ...,  0.0000, 22.2875,  0.0000],
        [20.5000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  5.5395,  0.0000,  0.0000]],
       grad_fn=<ReluBackward0>)
128 tensor([[ 3.9526,  0.0000,  9.4670,  ...,  0.0000,  0.00

100 tensor([[ 0.0000,  0.0000,  8.7974,  ...,  6.6581,  5.7384,  0.0000],
        [ 0.0000,  0.0000,  3.5487,  ..., 11.2767,  0.0000,  0.0000],
        [ 0.0000,  1.3337,  0.0000,  ...,  3.5287,  0.0000,  3.5953],
        ...,
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  3.8333,  1.3301,  ...,  3.1860,  0.0000,  1.5203],
        [ 0.0000,  0.0000, 10.5176,  ...,  0.0000,  0.0000,  0.0000]])
100 tensor([[ 0.0000,  4.2545,  0.0000,  ...,  6.2462,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  2.9766,  ..., 10.9778,  0.8712,  0.0000],
        [16.2490,  0.0000,  0.0000,  ..., 11.9242,  0.0000,  0.0000],
        ...,
        [ 0.0000,  0.0000, 14.6363,  ...,  0.0000,  0.0000,  3.7670],
        [ 4.9184,  0.0000,  0.0000,  ..., 16.9567,  0.0000,  4.1129],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000]])
100 tensor([[ 0.0000,  0.0000,  0.0000,  ..., 27.3949,  0.0000,  0.0000],
        [16.7116,  0.0000,  0.0000,  ...,  2.4681,

100 tensor([[ 1.9925,  0.0000, 16.5943,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  8.0919,  0.0000,  ...,  1.2980,  5.4243,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  8.2761,  0.0000,  0.0000],
        ...,
        [ 0.0000,  6.2475,  7.6446,  ...,  0.0000,  0.0000,  0.0000],
        [16.9908,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  7.5689,  ...,  0.9167,  0.0000,  0.0000]])
100 tensor([[ 0.0000,  2.7787,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  4.2030, 10.5239,  0.0000],
        [15.5756,  0.0000,  0.0000,  ...,  9.8500,  2.5031,  0.0000],
        ...,
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  6.0389],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  2.5761,  0.0000],
        [ 0.0000,  3.4143,  0.0000,  ...,  0.0000,  0.0000,  0.0000]])
100 tensor([[ 0.0000,  2.9321,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  5.7727,  0.0000,  ...,  0.0000,